<h1 id="how-to-use-this-document">How to use this document</h1>

<h2 id="what-is-org-mode">What is org-mode</h2>

<p>This is org-mode document. Org-mode is a markup language which allows
to write text documents containing executable code blocks.</p>

<p>Org-mode can do much more than this and you can find out more <a href="https://orgmode.org">here.</a></p>

<p>Org-mode works in emacs (the best editor in the world).</p>

<h2 id="code-blocks">Code blocks</h2>

<p>You can do two things with code blocks (besides simply reading
them):</p>

<ol>
<li><p>execute: this can be done using the <code>C-c C-c</code> (Ctrl-c
Ctrl-c) keybinding. The stdout of the code will be appended below the
code block itself</p></li>
<li><p>tangle: tangling a code block means creating a separate file that
contains the code which can thus be compiled and run as usual. If you
hit <code>C-c C-v C-t</code> (this call the emacs function
<code>org-babel-tangle</code>) all the code blocks in this file will be
tangled. If, instead, you only want to tangle a single code blocks, go
to that block and hit <code>C-u C-c C-v C-t</code></p></li>
</ol>

<h2 id="compiling-and-running-a-tangled-code-block">Compiling and
running a tangled code block</h2>

<p>Once you have tangled a code block, you can compile and run it like
any other code. For the code blocks of this document to work, you have
to use the following compile command:</p>

In [ ]:
gcc -fopenmp -I. aux.c code_block.c -o code_block

<p>And then you can run it by launching the <code>code_block</code>
executable</p>

In [ ]:
./code_block

<h2 id="some-other-useful-tricks">Some other useful tricks</h2>

<ul>
<li><p><strong>Set an environment variable</strong>: in order to set an
environment variable within emacs you have to hit
<code>M-x setenv</code> then write the name of the variable, hit enter,
write its value and hit enter again</p></li>
<li><p><strong>Refresh images in an org-mode document</strong>: if
images don't show up, use the command <code>M-x
 org-redisplay-inline-images</code></p></li>
<li><p><strong>Show this document as a presentation</strong>: to show
this document as a sequence of slides, you must install the emacs
<code>org-tree-slide</code> package. Then open the document and execute
the command <code>M-x
 org-tree-slide-mode</code>. You can mode forward and backward using the
<code>&gt;</code> and <code>&lt;</code> keys. The setup code at the
bottom of this file should automagically install this package upon
opening</p></li>
<li><p><strong>Export and org-mode document</strong>: Org-mode lets you
export org-mode documents in various formats such as pdf or html. Just
hit <code>C-c C-e</code> and follow the instructions.</p></li>
<li><p>When you open this document, the code block at the bottom (in the
Setup section) is supposed to be executed automatically to setup your
environment. If this does not happen (it may be the case in older emacs
version), just go there and hit <code>C-c C-c</code> to execute it
manually. Also, the two code blocks named <code>auxc</code> and
<code>auxh</code> are supposed to be tangled automatically. If this does
not happen, do it manually.</p></li>
</ul>

<h1 id="introduction">Introduction</h1>

<h2 id="parallel-computer-architectures">Parallel computer
architectures</h2>

<img src="figures/par_arch.png" width="700"/>

<p>Roughly speaking, parallel computers can be classified into two
types:</p>

<ol>
<li><p><strong>Shared memory</strong>: all the CPUs share one (logical)
memory, i.e., all processes can access the same addressing space
regardless of the CPU they are running on. This makes it simple to
communicate data from one process to another</p></li>
<li><p><strong>Distributed memory</strong>: the computer is actually
formed of multiple node, each having one or more CPUs and its own
memory. Nodes are connected through a network. A process running on one
node can only access data on the local memory; therefore, if it needs
data that is on another node, a message must be exchanged through the
network</p></li>
</ol>

<h2 id="shared-memory-smp-vs-numa">Shared memory: SMP vs NUMA</h2>

<p>One "logical memory" does not necessarily mean that only one physical
memory exists. If multiple memory modules exist, access to data may
non-uniform</p>

<ul>
<li>Symmetric Multi-Processor (SMP): all CPUs can access to all data
with the same bandwidth and latency</li>
<li>Non-Uniform Memory Access (NUMA): all CPUs can access to all data
but bandwidth and latency depends on where the data is placed</li>
</ul>

<img src="figures/numa.png" width="300"/>

<p>Both types of shared-memory architectures can be programmed using the
same tools and technologies. When performance is a concern, though,
special care must be taken for NUMA machines (we will not cover in this
course)</p>

<h2 id="multicore-processors-why">Multicore processors: why?</h2>

<p>Until the early 00's all processors had only one core (in fact we did
not use the word "core" at all). Then why have multicore processors
become ubiquitous? Energy consumption is the reason why:</p>

<p><span class="math inline"><em>P</em> = <em>C</em><em>V</em><sup>2</sup><em>f</em></span></p>

<p>however there is a linear dependence between <span class="math inline"><em>f</em></span> and <span class="math inline"><em>V</em></span>, therefore <span class="math inline"><em>P</em></span> grows as the cube of $f$!!!</p>

<p>Because the performance of single-core processors could only be
improved by increasing the frequency, this trend became
unsustainable.</p>

<p>Multicore processors design relies on <strong>Thread Level
Parallelism</strong> to improve performance. This means that more
transistors are used to assemble multiple execution units (i.e., cores)
on a single chip. This improves performance with only a linear increase
in the energy consumption: the capacitance <span class="math inline"><em>C</em></span> grows because of the increased
number of transistors.</p>

<p>In fact, it is also possible to produce faster processors which
consume less energy!!! Consider a quad-core processor with frequency
<span class="math inline">0.6<em>f</em></span>: it will be 2.4 times
faster and consume roughly 15\% less energy</p>

<h2 id="multicore-processors-why-1">Multicore processors: why?</h2>

<img src="figures/procs_history.png" width="900"/>

<h2 id="multicore-architecture">Multicore architecture</h2>

<p>Multicore computer: what does it look like?</p>

<p>The <code>hwloc</code> library is designed to retrieve all the
details of the architecture. For example, on my computer, I can run the
<code>lstopo</code> program from <code>hwloc</code> to retrieve the
architecture:</p>

In [ ]:
ssh plafrim lstopo --of png

![./figures/arch.png](./figures/arch.png)

<h2 id="how-to-program-multicore-computers">How to program multicore
computers?</h2>

<p>Many options exist, but they are not all simple, portable, efficient
etc.</p>

<p>Examples:</p>

<ul>
<li><p><strong>pThreads</strong> (POSIX Threads): difficult to use and
debug, not fully portable</p></li>
<li><p><strong>Intel TBB/OneAPI</strong>: proprietary</p></li>
<li><p><strong>Cilk</strong>: limited support and portability</p></li>
<li><p><strong>OpenMP</strong>: extremely portable, efficient,
relatively easy to use. huge community and support</p></li>
</ul>

<h1 id="the-openmp-standard">The OpenMP standard</h1>

<h2 id="basic-ideas-and-components">Basic ideas and components</h2>

<img src="figures/openmp_logo.png" width="500"/>

<p><strong>OpenMP</strong> (Open specifications for MultiProcessing) is
an Application Program Interface (API) to explicitly direct
multi-threaded, shared memory parallelism.</p>

<ul>
<li><p>First standard 1.0 was published in 1997</p></li>
<li><p>Latest standard is 5.2 published in November 2021</p>
<ul>
<li><p>Full specs are at this <a href="https://www.openmp.org/wp-content/uploads/OpenMP-API-Specification-5-2.pdf">URL</a></p></li>
<li><p>Examples and exercises are at this <a href="https://www.openmp.org/wp-content/uploads/openmp-examples-5.2.1.pdf">URL</a></p></li>
</ul></li>
<li><p>Many resources at <a href="https://www.openmp.org">https://www.openmp.org</a></p></li>
</ul>

<p>The OpenMP standard is developed by an advisory board that includes
many members from academia (UTK, LBNL, ANL, NASA,…) and industry (Intel,
AMD, NEC, Fujitsu, NVIDIA,…)</p>

<h2 id="basic-ideas-and-components-1">Basic ideas and components</h2>

<img src="figures/openmp_logo.png" width="500"/>

<ul>
<li>OpenMP is Comprised of three primary API components:
<ol>
<li><strong>Language directives</strong></li>
<li><strong>Runtime library routines</strong></li>
<li><strong>Environment variables</strong></li>
</ol></li>
<li>Portable:
<ul>
<li>Specifications for C/C++ and Fortran</li>
<li>Already available on many systems (including Linux, Win, IBM, SGI
etc.)</li>
</ul></li>
</ul>

<h2 id="disclaimer">Disclaimer</h2>

<img src="figures/openmp_logo.png" width="500"/>

<p>This course does not cover the whole OpenMP standard. The OpenMP
manual is over 600 pages as of today (v5.2)</p>

<p>Only a subset of constructs and clauses will be presented.</p>

<p>Tons of tutorials can be found online but better be used with
moderation.</p>

<h2 id="fork-join-execution-model">Fork-join execution model</h2>

<p>OpenMP is based on a fork-join execution model:</p>

<img src="figures/forkjoin.png" width="700"/>

<ul>
<li><p>Execution is started by a single thread called master
thread</p></li>
<li><p>when a parallel region is encountered, the master thread spawns a
set of threads</p></li>
<li><p>the set of instructions enclosed in a parallel region is
executed</p></li>
<li><p>at the end of the parallel region all the threads synchronize and
terminate leaving only the master</p></li>
</ul>

<h1 id="parallel-region">Parallel region</h1>

<h2 id="parallel-region-directive-syntax">Parallel region directive
syntax</h2>

In [ ]:
#pragma omp parallel [clause]
                     if (scalar or logical expression)
                     private(list)
                     firstprivate(list)
                     shared(list)
                     default(private | shared | none)
                     reduction(operator:list)
                     num_threads(scalar integer expression)
{
  /* Structured code block */
}

<ul>
<li><p>The <strong>master</strong> is a member of the team and has
thread number 0</p></li>
<li><p>Starting from the beginning of the region, the code is duplicated
and all threads will execute that code.</p></li>
<li><p>There is an <strong>implied barrier</strong> at the end of a
parallel section.</p></li>
<li><p>If any thread terminates within a parallel region, all threads in
the team will terminate.</p></li>
</ul>

<h2 id="a-simple-hello-world-example-in-openmp">A simple hello world
example in OpenMP</h2>

<p>Just a simple hello world with multiple threads:</p>

<ul>
<li><p>start with serial execution</p></li>
<li><p>open a parallel region where:</p>
<ul>
<li>each thread prints a message</li>
</ul></li>
</ul>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	#pragma omp parallel
	{
	  printf("Hello world!\n");
	}
}

<h2 id="a-slightly-more-complex-hello-world-example-in-openmp">A
slightly more complex hello world example in OpenMP</h2>

<p>Just a simple hello world with multiple threads:</p>

<ul>
<li><p>start with serial execution</p></li>
<li><p>open a parallel region where:</p>
<ul>
<li>each thread reads its identifier and the total number of threads
using, respectively, the <code>omp_get_thread_num()</code> and
<code>omp_get_num_threads()</code></li>
<li>prints a message</li>
</ul></li>
</ul>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	#pragma omp parallel
	{
	  printf("Hello world from thread %2d in a pool of %2d.\n", omp_get_thread_num(),
	         omp_get_num_threads());
	}
}

<h2 id="parallel-region-how-many-threads">Parallel region: how many
threads?</h2>

<p>How many threads do we have in the parallel regions of a code? The
number of threads depends on:</p>

<ul>
<li><p>Evaluation of the <code>if</code> clause (one or many)</p></li>
<li><p>Setting of the <code>num_threads</code> clause</p></li>
<li><p>Use of the <code>omp_set_num_threads()</code> library
function</p></li>
<li><p>Setting of the <code>OMP_NUM_THREADS</code> environment
variable</p></li>
<li><p>Implementation default - usually the number of CPUs on a node,
though it could be dynamic</p></li>
</ul>

<h2 id="parallel-region-how-many-threads-1">Parallel region: how many
threads?</h2>

<p>Complete example</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int iam, nth, n=5;
	
	#pragma omp parallel
	{
	  printf("Region 1 thread %2d / %2d.\n", omp_get_thread_num(), omp_get_num_threads());
	}
	
	omp_set_num_threads(n);
	
	#pragma omp parallel
	{
	  printf("Region 2 thread %2d / %2d.\n", omp_get_thread_num(), omp_get_num_threads());
	}
	
	#pragma omp parallel num_threads(2)
	{
	  printf("Region 3 thread %2d / %2d.\n", omp_get_thread_num(), omp_get_num_threads());
	}
	
	#pragma omp parallel if(n<5)
	{
	  printf("Region 4 thread %2d / %2d.\n", omp_get_thread_num(), omp_get_num_threads());
	}
	

}

<h2 id="hello-world-with-a-bug">Hello world with a bug</h2>

<p>Here is a minor variant of the hello world program…with a bug</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int iam, nth;
	
	#pragma omp parallel
	{
	  iam = omp_get_thread_num();
	  nth = omp_get_num_threads();
	  do_stuff(1);
	  printf("Hello world from thread %d in a pool of %2d.\n", iam, nth);
	}
}

<h2 id="data-sharing-12">Data sharing 1/2</h2>

<ul>
<li><p>Most variables are shared by default</p></li>
<li><p>Global variables include:</p>
<ul>
<li>Fortran: COMMON blocks, SAVE and MODULE variables</li>
<li>C: File scope variables, static</li>
</ul></li>
<li><p>Private variables include:</p>
<ul>
<li>Loop index variables (in !$OMP DO) constructs</li>
<li>Stack variables in subroutines called from parallel regions</li>
</ul></li>
<li><p>Fortran: Automatic variables within a statement block</p></li>
<li><p>The OpenMP Data Scope Attribute Clauses are used to explicitly
define how variables should be scoped. They include:</p>
<ul>
<li><code>private</code></li>
<li><code>firstprivate</code></li>
<li><code>shared</code></li>
<li><code>default</code></li>
<li><code>reduction</code></li>
</ul></li>
</ul>

<h2 id="data-sharing-22">Data sharing 2/2</h2>

<ul>
<li><p><code>private(list)</code>: a new object of the same type is
created for each thread (uninitialized!)</p></li>
<li><p><code>firstprivate(list)</code>: Listed variables are initialized
according to the value of their original objects prior to entry into the
parallel or work-sharing construct.</p></li>
<li><p><code>lastprivate(list)</code>: The value copied back into the
original variable object is obtained from the last (sequentially)
iteration or section of the enclosing construct.</p></li>
<li><p><code>shared(list)</code>: only one object exists in memory and
all the threads access it</p></li>
<li><p><code>default(shared|private|none)</code>: sets the default
scoping</p></li>
<li><p><code>reduction(operator:list)</code>: performs a reduction on
the variables that appear in its list.</p></li>
</ul>

<h2 id="hello-world-bugfix">Hello world bugfix</h2>

<p>Let's fix the bug: by declaring <code>iam</code> private, each thread
will have its own copy of this variable</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int iam, nth;
	
	#pragma omp parallel private(iam)
	{
	  iam = omp_get_thread_num();
	  nth = omp_get_num_threads();
	  do_stuff(1);
	  printf("Hello world from thread %d in a pool of %2d.\n", iam, nth);
	}
}

<h1 id="work-distribution-and-sharing">Work distribution and
sharing</h1>

<h2 id="dependencies">Dependencies</h2>

<h3 id="dependencies-1">Dependencies</h3>

<p>The interest of parallel programming is not to execute the same
workload multiple times but to distribute the workload to the available
processes so that execution time can be reduced. This implies that
multiple instructions will be executed <strong>concurrently</strong>
(or, equivalently, <strong>in parallel</strong>).</p>

<p>Two successive statements S1 and S2 can be executed concurrently if
they are <strong>independent</strong>. According to the
<strong>Bernstein conditions</strong> there exist three types of
dependencies:</p>

<ul>
<li><p><strong>Read-After-Write</strong> or <strong>true
dependency</strong> or <strong>flow dependency</strong>: if
<code>Input(S2)</code> overlaps with <code>Output(S1)</code></p></li>
<li><p><strong>Write-After-Read</strong> or
<strong>anti-dependency</strong>: if <code>Output(S2)</code> overlaps
with <code>Input(S1)</code></p></li>
<li><p><strong>Write-After-Write</strong> or <strong>output
dependency</strong>: if <code>Output(S2)</code> overlaps with
<code>Output(S1)</code></p></li>
</ul>

<h3 id="dependencies-2">Dependencies</h3>

<p>Example. Are these two statements independent?</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	a = b+c;
	e = d+a;
}

<p>What kind of dependency is there? RAW. Here is a more convoluted
example</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	for(i=1; i<n; i++)
	  x[i] += x[i-1];
}

<h3 id="dependencies-3">Dependencies</h3>

<p>Example. Are these two statements independent?</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	a = b+c;
	b = c*2;
}

<p>What kind of dependency is there? WAR. Note that WAR dependencies can
be sometimes removed!</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	d = b;
	a = d+c;
	b = c*2;
}

<p>Now the second and third statement have become independent. Here is a
more convoluted example</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	for(i=0; i<n-1; i++)
	  x[i] += x[i+1];
}

<h3 id="dependencies-4">Dependencies</h3>

<p>Example. Are these two statements independent?</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	c = a+b;
	c = 2;
}

<p>What kind of dependency is there? WAW. Here is a more convoluted
example</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	for(i=0; i<n; i++)
	  c += x[i];
}

<h2 id="master">Master</h2>

<p>The <code>master</code> directive identifies a code block which is
only executed by the master thread</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int iam;
	
	#pragma omp parallel private(iam)
	  {
	    iam = omp_get_thread_num();
	
	#pragma omp master
	    {
	      do_stuff(0.1);
	      printf(" ---> This is only done by: %2d\n",iam);
	    }
	    printf("      This is also done by: %2d.\n",iam);
	  }
}

<h2 id="single">Single</h2>

<p>The <code>single</code> directive identifies a code block which is
only executed by one (any) thread</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int iam;
	
	#pragma omp parallel private(iam)
	  {
	    iam = omp_get_thread_num();
	
	#pragma omp single
	    {
	      do_stuff(0.1);
	      printf(" ---> This is only done by: %2d\n",iam);
	    }
	    printf("      This is also done by: %2d.\n",iam);
	  }
}

<h2 id="single-vs-master">Single vs master</h2>

<p>One obvious difference between <code>single</code> and
<code>master</code> is that with <code>master</code> only the thread
with id 0 can execute the code block. This has a risk: you have to make
sure that the master thread passes by that code block otherwise it will
never be executed.</p>

<p>Can you spot any other difference from executing the two code blocks
above? There is an <strong>implied barrier</strong> at the end of the
<code>single</code> block. It can be removed using the
<code>nowait</code> clause</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int iam;
	
	#pragma omp parallel private(iam)
	  {
	    iam = omp_get_thread_num();
	
	#pragma omp single nowait
	    {
	      do_stuff(0.1);
	      printf(" ---> This is only done by: %2d\n",iam);
	    }
	    printf("      This is also done by: %2d.\n",iam);
	  }
}

<h2 id="parallel-loops">Parallel loops</h2>

<h3 id="parallel">Parallel</h3>

<p>In the code below, all the iterations in the loop are
<strong>independent</strong>. This means that they can be executed
<strong>concurrently</strong>. However the code below is wrong because
it does not produce the same result as in sequential</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int i, n=4;
	int a[n], b[n], c[n];
	
	#pragma omp parallel private(i)
	{
	
	  for (i=0; i<n; i++) {
	    printf("Thread %2d does iteration %2d\n",omp_get_thread_num(),i);
	    a[i] += b[i]+c[i];
	  }
	}
}

<h3 id="parallel-1">Parallel</h3>

<p>OpenMP provides a construct that automatically parallelizes loops by
executing chunks of iterations concurrently. Note that the loop index
<code>i</code> is implicitly <code>private</code>.</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int i, n=4;
	int a[n], b[n], c[n];
	
	#pragma omp parallel
	{
	#pragma omp for
	  for (i=0; i<n; i++) {
	    printf("Thread %2d does iteration %2d\n",omp_get_thread_num(),i);
	    a[i] += b[i]+c[i];
	  }
	}
}

<h3 id="schedule">Schedule</h3>

<p>The <code>schedule</code> clause in the <code>for</code> construct
specifies how the iterations of the loop are assigned to threads:</p>

<ul>
<li><p><code>static</code>: loop iterations are divided into pieces of
size chunk and then statically assigned to threads in a round-robin
fashion</p></li>
<li><p><code>dynamic</code>: loop iterations are divided into pieces of
size chunk, and dynamically scheduled among the threads; when a thread
finishes one chunk, it is dynamically assigned another</p></li>
<li><p><code>guided</code>: for a chunk size of 1, the size of each
chunk is proportional to the number of unassigned iterations divided by
the number of threads, decreasing to 1. For a chunk size with value k
(greater than 1), the size of each chunk is determined in the same way
with the restriction that the chunks do not contain fewer than k
iterations</p></li>
<li><p><code>runtime</code>: The scheduling decision is deferred until
runtime by the environment variable OMP SCHEDULE</p></li>
</ul>

<h3 id="schedule-1">Schedule</h3>

<p>Let's see how <code>schedule</code> works:</p>

In [ ]:
int i;
#pragma omp parallel for num_threads(4) schedule(guided,25)
for (i=0; i<400; i++)
  printf("%3d  %2d\n",i,omp_get_thread_num());

![res.data](res.data)

![./figures/scheds.png](./figures/scheds.png)

<h3 id="collapse">Collapse</h3>

<p>The <code>collapse</code> clause allows for combining multiple loops
into a single one and for parallelizing its iterations. The number of
loops to collapse can be provided as an option</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int i, j;
	
	#pragma omp parallel for private(i,j) collapse(2)
	for (i=0; i<2; i++) {
	  for (j=0; j<4; j++) {
	printf("Thread %2d does iteration i:%2d j:%2d\n",omp_get_thread_num(),i,j);
	  }
	}
}

<h1 id="threads-synchronization">Threads synchronization</h1>

<h2 id="barriers">Barriers</h2>

<h3 id="barrier">Barrier</h3>

<p>A barrier is simply a waiting point: all threads must wait for all
the others to reach a barrier point before moving on. Example</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int iam;
	  double t=secs();
	#pragma omp parallel private(iam)
	  {
	    iam = omp_get_thread_num();
	
	    if(iam==0){
	  do_stuff(0.5); // 0.5 seconds
	    } else {
	  do_stuff(0.3); // 0.3 seconds
	    }
	#pragma omp barrier
	    printf("Thread %2d reached this point at time %f.\n",iam,secs()-t);
	  }
}

<h3 id="barrier-1">Barrier</h3>

<p>Improper use of barriers can cause <strong>deadlocks</strong>: if not
all threads pass by the barrier, those who do will be waiting
forever…</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int iam;
	  double t=secs();
	#pragma omp parallel private(iam)
	  {
	    iam = omp_get_thread_num();
	
	    if(iam==0){
	  do_stuff(0.5);
	    } else {
	  do_stuff(0.3);
	      #pragma omp barrier
	    }
	
	    printf("Thread %2d reached this point at time %f.\n",iam,secs()-t);
	  }
}

<h2 id="critical-sections">Critical sections</h2>

<h3 id="critical">Critical</h3>

<p>The <code>critical</code> directive identifies a code block which is
executed in <strong>mutual exclusion</strong> by all threads, i.e., one
at a time.</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int iam;
	  double t=secs();
	
	#pragma omp parallel private(iam)
	  {
	    iam = omp_get_thread_num();
	
	#pragma omp critical
	    {
	      do_stuff(0.1);
	      printf("This is done by %2d  at time %f\n",iam, secs()-t);
	    }
	  }
}

<h3 id="critical-scope">Critical scope</h3>

<p>Critical sections can have names. The name argument is used to
identify the critical construct. For any critical construct for which
name is not specified, the effect is as if an identical (unspecified)
name was specified. It is not possible to have two or more threads in
different critical regions that have the same name!</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int iam;
	  double t=secs();
	
	#pragma omp parallel private(iam)
	  {
	    iam = omp_get_thread_num();
	
	#pragma omp critical (toto)
	    {
	      do_stuff(0.1);
	      printf("First  is done by %2d  at time %f\n",iam, secs()-t);
	    }
	
	#pragma omp critical (titi)
	    {
	      do_stuff(0.1);
	      printf("Second is done by %2d  at time %f\n",iam, secs()-t);
	    }
	  }
}

<h2 id="atomic-instructions">Atomic instructions</h2>

<h3 id="atomic">Atomic</h3>

<p>The atomic construct ensures that a specific storage location is
accessed atomically so that possible simultaneous reads and writes by
multiple threads do not result in indeterminate values. Five types of
atomic constructs exist: <code>read</code>, <code>write</code>,
<code>update</code>, <code>capture</code> and <code>compare</code></p>

<ul>
<li><code>read</code>: atomically read a memory location, i.e.,
<code>x</code> can not change while being read</li>
</ul>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int x, v;
	
	#pragma omp parallel
	  {
	    #pragma atomic read
	    v = x;
	  }
}

<h3 id="atomic-1">Atomic</h3>

<ul>
<li><p><code>write</code>: atomically write a memory location</p></li>
<li><p><code>update</code>: atomically update (i.e. read-modify-write) a
memory location</p></li>
</ul>

<p>So what's the interest of atomic? take this example: we could
certainly use <code>critical</code> to protect the update of
<code>x[]</code> but this would prevent calls to
<code>compute_one</code> to be executed concurrently. With
<code>atomic</code> only the update of <code>x[]</code> is
serialized.</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	double t_start=secs(), t_end;
	  int i, n=100, m=5, tot=0, x[5]={0,0,0,0,0};
	
	#pragma omp parallel for
	    for(i=0; i<n; i++){
	#pragma omp atomic update
	      x[rnd_int()%m] += compute_one(0.01);
	    }
	  t_end = secs()-t_start;
	
	  for(i=0; i<m; i++)
	    tot += x[i];
	  printf("\nTot:%10d   time:%f\n",tot, t_end);
}

<h3 id="atomic-2">Atomic</h3>

<ul>
<li><code>capture</code>: atomically update a memory location and
capture its initial or final value</li>
</ul>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int x, v, y, w;
	
	#pragma omp parallel
	  {
	    /* Capture initial value */
	    #pragma atomic capture
	    v = x++;
	
	    /* Capture final value */
	    #pragma atomic capture
	    w = ++y;
	
	  }
}

<h3 id="atomic-3">Atomic</h3>

<ul>
<li><code>compare</code>: atomically and conditionally update a memory
location</li>
</ul>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int i, n=1000, min=99999999;
	int x[n];  
	
	rand_fill(x, n);
	
	#pragma omp parallel for
	for(i=0; i<n; i++){
	  #pragma omp atomic compare
	  if (x[i] < min) { min = x[i]; }
	  }
	
	printf("Min is %d\n",min);

}

<h2 id="reductions">Reductions</h2>

<h3 id="reductions-1">Reductions</h3>

<p>Assume this simple code that computes the sum of all the elements of
an array</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int i, sum, n=1000;
	int x[n];  
	
	rand_fill(x, n); sum=0;
	
	
	for(i=0; i<n; i++){
	   sum += x[i];
	}
	
	printf("Sum is %d\n",sum);

}

<p>The iterations of this loop are clearly dependent because of the
updates on <code>sum</code>. We could actually use a critical section or
an atomic update but we would loose all performance.</p>

<h3 id="reductions-2">Reductions</h3>

<p><strong>Reductions</strong> allow us to take advantage of
associativity and commutativity of some operators (+ in this case):</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int i, sum, n=1000;
	    int x[n];  
	
	    rand_fill(x, n); sum=0;
	
	#pragma omp parallel reduction(+:sum)
	    {
	#pragma omp for 
	      for(i=0; i<n; i++){
	        sum += x[i];
	      }
	      printf("Partial Sum on %d is %d\n",omp_get_thread_num(),sum);
	    }
	    printf("Sum is %d\n",sum);

}

<p>The reduction clause specifies an operator and one or more list
items. For each list item, a private copy is created in each implicit
task, and is initialized appropriately for the operator. After the end
of the region, the original list item is updated with the values of the
private copies using the specified operator.</p>

<h3 id="reductions-3">Reductions</h3>

<p>For the <code>C</code> language, predefined reduction operators are
(note that : in the table below is actually a | )</p>

<table>
<thead>
<tr class="header">
<th>Operator</th>
<th>Initializer</th>
<th>Combiner</th>
</tr>
</thead>
<tbody>
<tr class="odd">
<td>+</td>
<td>omp<sub>priv</sub>=0</td>
<td>omp<sub>out</sub> += omp<sub>in</sub></td>
</tr>
<tr class="even">
<td>*</td>
<td>omp<sub>priv</sub>=1</td>
<td>omp<sub>out</sub> *= omp<sub>in</sub></td>
</tr>
<tr class="odd">
<td>~</td>
<td>omp<sub>priv</sub>=~0</td>
<td>omp<sub>out</sub> ~= omp<sub>in</sub></td>
</tr>
<tr class="even">
<td>:</td>
<td>omp<sub>priv</sub>=0</td>
<td>omp<sub>out</sub> := omp<sub>in</sub></td>
</tr>
<tr class="odd">
<td>^</td>
<td>omp<sub>priv</sub>=0</td>
<td>omp<sub>out</sub> ^= omp<sub>in</sub></td>
</tr>
<tr class="even">
<td>&amp;&amp;</td>
<td>omp<sub>priv</sub>=1</td>
<td>omp<sub>out</sub> = omp<sub>in</sub> &amp;&amp;
omp<sub>out</sub></td>
</tr>
<tr class="odd">
<td>::</td>
<td>omp<sub>priv</sub>=0</td>
<td>omp<sub>out</sub> = omp<sub>in</sub> :: omp<sub>out</sub></td>
</tr>
<tr class="even">
<td>max</td>
<td>omp<sub>priv</sub>=minval</td>
<td>omp<sub>out</sub> = max(omp<sub>in</sub>,omp<sub>out</sub>)</td>
</tr>
<tr class="odd">
<td>min</td>
<td>omp<sub>priv</sub>=maxval</td>
<td>omp<sub>out</sub> = min(omp<sub>in</sub>,omp<sub>out</sub>)</td>
</tr>
</tbody>
</table>

<h1 id="tasks">Tasks</h1>

<h2 id="task">Task</h2>

<p>The OpenMP <code>task</code> construct simply identifies a block of
code which is ready to be executed and whose execution is
<strong>deferred</strong>. Once the task is created, it can be executed
<strong>by any thread, at any time</strong>. This means that we can not
make any assumptions on when a task is executed and by which thread and
in which order all the created tasks are executed.</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	#pragma omp parallel
	 {
	#pragma omp single
	   {
	 #pragma omp task
	     printf("Thead %2d does task 1\n",omp_get_thread_num());
	
	 #pragma omp task
	     printf("Thead %2d does task 2\n",omp_get_thread_num());
	
	 #pragma omp task
	     printf("Thead %2d does task 3\n",omp_get_thread_num());
	
	 #pragma omp task
	     printf("Thead %2d does task 4\n",omp_get_thread_num());
	   }
	 }
}

<p>Why do we need the <code>master</code> construct in the code
above?</p>

<h2 id="task-data">Task data</h2>

<p>A slightly more complex example, with a bug:</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int i;
	printf("Hello %p\n",&i);
	#pragma omp parallel private(i)
	{
	#pragma omp master
	  {
	    for(i=0; i<6; i++)
	      {
	#pragma omp task
	        printf("Thread  %d   iteration: %d\n", omp_get_thread_num(), i);
	      }
	  }
	}
}

<p>What went wrong?</p>

<h2 id="task-data-1">Task data</h2>

<p>The value of shared variables accessed within a task might change
between the creation of the task and its actual execution. Some clauses
can be used to define the scope of variables within tasks:</p>

<ul>
<li><p><code>shared(x)</code> means that when the task is executed x is
the same variable (the same memory location) as when the task was
created</p></li>
<li><p><code>firstprivate(x)</code> means that x is private to the task,
i.e., when the task is created, a brand new variable x is created as
well and its value is set to be the same as the value of x in the
enclosing context at the moment when the task is created. This new copy
is destroyed when the task is finished</p></li>
<li><p><code>private(x)</code> means that x is private to the task,
i.e., when the task is created, a brand new variable x is created as
well. This new copy is destroyed when the task is finished</p></li>
</ul>

<p>If a variable is <code>private</code> in the parallel region it is
implicitly <code>firstprivate</code> in the included tasks</p>

<h2 id="task-data-2">Task data</h2>

<p>A slightly more complex example, with a bugfix:</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int i;
	printf("Hello %p\n",&i);
	#pragma omp parallel
	{
	#pragma omp master
	  {
	    for(i=0; i<6; i++)
	      {
	#pragma omp task firstprivate(i)
	        printf("Thread  %d   iteration: %d\n", omp_get_thread_num(), i);
	      }
	  }
	}
}

<h2 id="task-if">Task if</h2>

<p>Creating and handling tasks has a cost. Therefore, it is not always
worth creating a task, for example, if the task has only little work to
do. The <code>if</code> clause can be used to choose whether to create a
task or immediately run the code block</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	double w=0.5;
	
	#pragma omp parallel
	{
	#pragma omp master
	  {
	#pragma omp task
	    printf("Thread  %d executes this first task\n", omp_get_thread_num());
	
	#pragma omp task if(w>0.4)
	    {
	      do_stuff(w);
	      printf("Thread  %d executes this second task\n", omp_get_thread_num());
	    }
	
	  }
	}
}

<h2 id="taskwait">Taskwait</h2>

<p>So how can we be sure that some tasks are actually executed? The
<code>taskwait</code> directive ensures that all the previously
submitted tasks have been executed. Note that this does not include
descendants, i.e., tasks that have been generated by other tasks.</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int x, y, z;
	
	#pragma omp parallel
	{
	#pragma omp master
	  {
	#pragma omp task
	    x = compute_one(0.2);
	
	#pragma omp task
	    y = compute_one(0.2);
	
	#pragma omp taskwait
	    z = x+y;
	    printf("z is %d\n", z);
	  }
	}
}

<h2 id="task-dependencies">Task dependencies</h2>

<p>It is possible to define an execution order by specifying task
<strong>dependencies</strong>. This is done through the
<code>depend</code> clause and the Bernstein conditions:</p>

<ul>
<li><p>The <code>in</code> dependence-type. The generated task will be a
dependent task of all previously generated sibling tasks that reference
at least one of the list items in an <code>out</code> or
<code>inout</code> dependence-type list.</p></li>
<li><p>The <code>out</code> and <code>inout</code> dependence-types. The
generated task will be a dependent task of all previously generated
sibling tasks that reference at least one of the list items in an
<code>in</code>, <code>out</code>, or <code>inout</code> dependence-type
list.</p></li>
</ul>

<h2 id="task-dependencies-1">Task dependencies</h2>

<p>Example:</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int a, b, c, x, y;
	double t=secs();
	#pragma omp parallel
	{
	#pragma omp master
	  {
	#pragma omp task depend(out:a)
	    a = f_a();
	
	#pragma omp task depend(out:b)
	    b = f_b();
	
	#pragma omp task depend(out:c)
	    c = f_c();
	
	#pragma omp task depend(in:b,c) depend(out:x)
	    x = f_x(b, c);
	
	#pragma omp task depend(in:a,x) depend(out:y)
	    y = f_y(a, x);
	
	#pragma omp taskwait
	    printf("y: %d (correct value is 9) and time is %f\n",y,secs()-t);
	  }
	}
}

<p>Can you draw the dependency graph?</p>

<h2 id="task-priorities">Task priorities</h2>

<p>Assuming only two threads are available and all functions take one
second, the following two schedulings are possible.</p>

<img src="figures/sched.png" width="600"/>

<h2 id="task-priorities-1">Task priorities</h2>

<p>The <code>priority</code> clause can be used to give the OpenMP
scheduler a hint on the importance of a task</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int a, b, c, x, y;
	double t=secs();
	#pragma omp parallel
	{
	#pragma omp master
	  {
	#pragma omp task depend(out:b) priority(2)
	    b = f_b();
	
	#pragma omp task depend(out:c) priority(2)
	    c = f_c();
	
	#pragma omp task depend(out:a)
	    a = f_a();
	
	#pragma omp task depend(in:b,c) depend(out:x)
	    x = f_x(b, c);
	
	#pragma omp task depend(in:a,x) depend(out:y)
	    y = f_y(a, x);
	
	#pragma omp taskwait
	    printf("y: %d (correct value is 9) and time is %f\n",y,secs()-t);
	  }
	}
}

<h2 id="task-dependencies-and-pointers">Task dependencies and
pointers</h2>

<p>When using pointers to specify dependencies, you should dereference
it to make sure the dependence is inferred from the pointed data rather
than the pointer variable.</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int x[2]={0,0};
	int *p=x;
	double t=secs();
	#pragma omp parallel
	{
	#pragma omp master
	  {
	#pragma omp task firstprivate(p) depend(out:*p)
	    *p = compute_one(1.0);
	
	    p+=1;
	
	#pragma omp task firstprivate(p) depend(out:*p)
	    *p = compute_one(1.0);
	
	#pragma omp taskwait
	    printf("x: {%d,%d} (correct value is {1,1}) and time is %f\n",x[0],x[1],secs()-t);
	  }
	}
}

<h1 id="locks">Locks</h1>

<h2 id="locks-1">Locks</h2>

<p>A lock is a data of type <code>omp_lock_t</code> which can be used to
prevent simultaneous access to shared resources according to the
schema</p>

<ul>
<li><p>acquire (or set or lock) the lock</p></li>
<li><p>access data</p></li>
<li><p>release (on unset or unlock) the lock</p></li>
</ul>

<p>Acquisition of the lock is exclusive in the sense that only one
threads can hold the lock at a given time. A lock can be in one of the
following states:</p>

<ul>
<li><p><strong>uninitialized</strong>: the lock is not active and cannot
be acquired/released by any thread;</p></li>
<li><p><strong>unlocked</strong>: the lock has been initialized and can
be acquired by any thread;</p></li>
<li><p><strong>locked</strong>: the lock has been acquired by one thread
and cannot be acquired by any other thread until the owner releases
it.</p></li>
</ul>

<h2 id="locks-2">Locks</h2>

<p>Transitions through states can be achieved with the following
routines</p>

<ul>
<li><p><code>omp_init_lock</code>: initializes a lock</p></li>
<li><p><code>omp_destroy_lock</code>: uninitializes a lock</p></li>
<li><p><code>omp_set_lock</code>: waits until a lock is available, and
then sets it</p></li>
<li><p><code>omp_unset_lock</code>: unsets a lock</p></li>
<li><p><code>omp_test_lock</code>: tests a lock, and sets it if it is
available</p></li>
</ul>

<h2 id="locks-3">Locks</h2>

<p>Example</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	omp_lock_t lock;
	omp_init_lock(&lock);
	
	#pragma omp parallel
	{
	  omp_set_lock(&lock);
	  printf("%d: It's my turn to use the resource\n",omp_get_thread_num());
	  use_resource();
	  omp_unset_lock(&lock);
	}
	
	omp_destroy_lock(&lock);
}

<h2 id="locks-4">Locks</h2>

<p>Example with test lock</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	omp_lock_t lock;
	omp_init_lock(&lock);
	
	#pragma omp parallel
	{
	
	  while(!omp_test_lock(&lock)){
	    /* if lock is already locked, I do some other useful stuff */
	    printf("%d: lock is busy, I do some stuff\n",omp_get_thread_num());
	    do_stuff(0.5);
	  }
	
	  printf("%d: It's my turn to use the resource\n",omp_get_thread_num());
	  use_resource();
	  omp_unset_lock(&lock);
	}
	
	omp_destroy_lock(&lock);
}

<h1 id="mistakes-to-avoid">Mistakes to avoid</h1>

<h2 id="add-useless-loops">Add useless loops</h2>

<p>Do not create a new loop just for the purpose of parallelizing it</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	#pragma omp parallel
	{
	  nth = omp_get_num_threads();
	#pragma omp for
	  for(i=0; i<nth; i++){
	    do_stuff();
	  }
	}
}

<p>This is exactly the same as</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	#pragma omp parallel
	{
	  do_stuff();
	}
}

<h2 id="use-tasks-with-caution">Use tasks with caution</h2>

<img src="figures/rambo.jpg" width="500"/>

<p>Tasks have a <strong>relatively high overhead</strong> and should be
used with caution.</p>

<ul>
<li>creating a task for a few operations is probably a very bad
idea</li>
<li>try to combine as many operations as possible into a single task as
long as this does not reduce parallelism</li>
</ul>

<h2 id="minimize-critical-sections">Minimize critical sections</h2>

<p>Critical sections serialize the work of processes.</p>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	#pragma omp parallel for
	  for(i=0; i<n; i++){
	#pragma omp critical
	    do_stuff();
	  }
}

<p>The code above is completely sequential. The execution time will be
the same as without the parallelization but the iterations will be done
in a different order.</p>

<ul>
<li>separate what really needs to be in the critical section from what
can be done in parallel</li>
<li>sometimes atomic instructions can be used instead of critical</li>
</ul>

<h2 id="dont-forget-the-parallel-section">Don't forget the parallel
section</h2>

<p>Stupid to say but there is no parallelism if you don't put a parallel
section somewhere. Just don't forget.</p>

<p>Conversely, if you can merge multiple parallel sections into a single
one, it might be good to do so in order to reduce overhead</p>

<h1 id="aux-code">Aux code</h1>

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int seed=-1;
	  #pragma omp threadprivate(seed)
	
	  int rnd_int() {
	    // & 0x7fffffff is equivalent to modulo with RNG_MOD = 2^31
	#if defined(_OPENMP)
	    if(seed==-1) seed = omp_get_thread_num()+1;
	#else
	    if(seed==-1) seed = 1;
	#endif
	    return (seed = (seed * 1103515245 + 12345) & 0x7fffffff);
	  }
	
	  void rand_fill(int *x, int n){
	    int i;
	    for(i=0; i<n; i++){
	      x[i]=rnd_int()%n-n/2;
	    }
	  }
	
	  long usecs (){
	    struct timeval t;
	
	    gettimeofday(&t,NULL);
	    return t.tv_sec*1000000+t.tv_usec;
	  }
	
	  double secs (){
	    struct timeval t;
	
	    gettimeofday(&t,NULL);
	    return ((double)(t.tv_sec*1000000+t.tv_usec))/1000000.0;
	  }
	
	  void do_stuff(double sec){
	
	    long s, e;
	    s=0; e=0;
	    s = usecs();
	    while(((double) e-s)/1000000 < sec)
	      {
	        e = usecs();
	      }
	    return;
	  }
	
	  int compute_one(double sec){
	    do_stuff(sec);
	    return 1;
	  }
	
	  int f_a(){
	    do_stuff(1.0);
	    return 1;
	  }
	
	  int f_b(){
	    do_stuff(1.0);
	    return 2;
	  }
	
	  int f_c(){
	    do_stuff(1.0);
	    return 3;
	  }
	
	  int f_x(int b, int c){
	    do_stuff(1.0);
	    return b+c+1;
	  }
	
	  int f_y(int a, int x){
	    do_stuff(1.0);
	    return a+x+2;
	  }
	
	  void use_resource(){
	    do_stuff(1.0);
	    return;
	  }

}

In [ ]:
//%cflags:-fopenmp
#include <omp.h>
#include <stdio.h>
#include <unistd.h>
#include <sys/time.h>
#include <stdlib.h>

#include <omp.h>
#include <stdio.h>
#include <stdlib.h>

int main(int argc, char* argv[]){
	int rnd_int();
	void rand_fill(int *x, int n);
	long usecs ();
	double secs ();
	void do_stuff(double sec);
	int compute_one(double sec);
	int f_a();
	int f_b();
	int f_c();
	int f_x(int b, int c);
	int f_y(int a, int x);
	void use_resource();
}